# 🔥 Sistema Inteligente de Monitoramento e Predição de Queimadas no Pantanal
## Aplicações em Aprendizado de Máquina - Ciência de Dados

---

### 📋 Sumário Executivo

**Contexto:** O Pantanal, maior planície alagável do mundo e patrimônio natural da humanidade, enfrentou nos últimos anos algumas das piores temporadas de queimadas de sua história. Este projeto desenvolve um sistema inteligente de análise e predição utilizando dados geoespaciais reais de focos de calor.

**Objetivos:**
- Analisar padrões espaço-temporais de queimadas no Pantanal (2020-2024)
- Comparar evolução das queimadas entre diferentes anos e meses
- Identificar clusters naturais de focos com características similares
- Desenvolver modelos preditivos para antecipação de ocorrências
- Gerar insights acionáveis para políticas de prevenção e combate

**Metodologia:**
- Análise Exploratória de Dados (EDA)
- Processamento Individual e em Lote (Multi-Ano)
- Aprendizado Não Supervisionado (K-Means, DBSCAN)
- Aprendizado Supervisionado (Random Forest, XGBoost)
- Visualização Geoespacial Avançada

**Datasets:** 
- Fonte: INPE - Instituto Nacional de Pesquisas Espaciais
- Período: 01/01/2020 a 31/12/2024 (5 anos disponíveis)
- Tipo: Dados Geoespaciais de Focos de Calor
- Modo: Processamento Individual ou em Lote (selecionável)

---

## 1️⃣ Configuração do Ambiente e Importação de Bibliotecas

### 1.1 Instalação de Dependências (Google Colab)

In [1]:
# Instalar bibliotecas necessárias no Google Colab
%pip install -q geopandas folium plotly xgboost scikit-learn pandas numpy matplotlib seaborn

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.2 -> 25.3
[notice] To update, run: python.exe -m pip install --upgrade pip


### 1.2 Importação de Bibliotecas

In [2]:
# Manipulação e análise de dados
import pandas as pd
import numpy as np
from datetime import datetime
import warnings
warnings.filterwarnings('ignore')

# Visualização
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Importar display para exibição de DataFrames
from IPython.display import display

# Widgets interativos
try:
    import ipywidgets as widgets
    from IPython.display import clear_output
    WIDGETS_AVAILABLE = True
    print("✅ IPyWidgets disponível para seleção interativa")
except ImportError:
    WIDGETS_AVAILABLE = False
    print("⚠️ IPyWidgets não disponível - usando configuração manual")

# Análise geoespacial
try:
    import geopandas as gpd
    print("✅ GeoPandas disponível")
except ImportError:
    print("⚠️ GeoPandas não disponível - análises geoespaciais limitadas")

import folium
from folium.plugins import HeatMap, MarkerCluster

# Machine Learning - Pré-processamento
from sklearn.preprocessing import StandardScaler, LabelEncoder, MinMaxScaler
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV
from sklearn.impute import SimpleImputer

# Machine Learning - Algoritmos Não Supervisionados
from sklearn.cluster import KMeans, DBSCAN, AgglomerativeClustering
from sklearn.metrics import silhouette_score, davies_bouldin_score, calinski_harabasz_score

# Machine Learning - Algoritmos Supervisionados
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.tree import DecisionTreeClassifier
import xgboost as xgb

# Machine Learning - Métricas
from sklearn.metrics import (
    classification_report, confusion_matrix, accuracy_score,
    precision_score, recall_score, f1_score, roc_auc_score, roc_curve,
    mean_squared_error, mean_absolute_error, r2_score
)

# Configurações de visualização - com fallback para compatibilidade
try:
    plt.style.use('seaborn-v0_8-darkgrid')
except OSError:
    try:
        plt.style.use('seaborn-darkgrid')
    except OSError:
        plt.style.use('ggplot')
        print("⚠️ Estilo seaborn não disponível, usando ggplot")

sns.set_palette("husl")
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)

print("✅ Todas as bibliotecas importadas com sucesso!")
print(f"📊 Versões principais:")
print(f"   - Pandas: {pd.__version__}")
print(f"   - NumPy: {np.__version__}")
import sklearn
print(f"   - Scikit-learn: {sklearn.__version__}")

✅ IPyWidgets disponível para seleção interativa
✅ GeoPandas disponível
✅ Todas as bibliotecas importadas com sucesso!
📊 Versões principais:
   - Pandas: 2.3.3
   - NumPy: 2.3.3
   - Scikit-learn: 1.7.2


## 2️⃣ Configuração de Datasets e Modo de Processamento

### 2.1 Definição dos Datasets Disponíveis

In [3]:
# =============================================================================
# CONFIGURAÇÃO DE DATASETS MULTI-ANO
# =============================================================================

# Diretório base dos arquivos CSV (ajuste conforme necessário)
import os

# Detectar se está no Google Colab ou ambiente local
try:
    import google.colab
    IS_COLAB = True
    BASE_PATH = ""  # No Colab, usar URLs
except ImportError:
    IS_COLAB = False
    # Caminho local para os arquivos CSV
    BASE_PATH = r"c:\Users\Workstation\Desktop\Jupyter Notebook (.ipynb)\Data Storage (.csv)"

# Dicionário com todos os datasets disponíveis
DATASETS_DISPONIVEIS = {
    2020: {
        'url': 'https://media.githubusercontent.com/media/OpenScienceTechnology/Dataset/refs/heads/main/bdqueimadas_2020-01-01_2020-12-31.csv',
        'arquivo_local': os.path.join(BASE_PATH, 'bdqueimadas_2020-01-01_2020-12-31.csv'),
        'descricao': 'Queimadas 2020 - Ano crítico no Pantanal'
    },
    2021: {
        'url': 'https://media.githubusercontent.com/media/OpenScienceTechnology/Dataset/refs/heads/main/bdqueimadas_2021-01-01_2021-12-31.csv',
        'arquivo_local': os.path.join(BASE_PATH, 'bdqueimadas_2021-01-01_2021-12-31.csv'),
        'descricao': 'Queimadas 2021'
    },
    2022: {
        'url': 'https://media.githubusercontent.com/media/OpenScienceTechnology/Dataset/refs/heads/main/bdqueimadas_2022-01-01_2022-12-31.csv',
        'arquivo_local': os.path.join(BASE_PATH, 'bdqueimadas_2022-01-01_2022-12-31.csv'),
        'descricao': 'Queimadas 2022'
    },
    2023: {
        'url': 'https://media.githubusercontent.com/media/OpenScienceTechnology/Dataset/refs/heads/main/bdqueimadas_2023-01-01_2023-12-31.csv',
        'arquivo_local': os.path.join(BASE_PATH, 'bdqueimadas_2023-01-01_2023-12-31.csv'),
        'descricao': 'Queimadas 2023'
    },
    2024: {
        'url': 'https://media.githubusercontent.com/media/OpenScienceTechnology/Dataset/refs/heads/main/bdqueimadas_2024-01-01_2024-12-31.csv',
        'arquivo_local': os.path.join(BASE_PATH, 'bdqueimadas_2024-01-01_2024-12-31.csv'),
        'descricao': 'Queimadas 2024'
    }
}

# CONFIGURAÇÃO: Usar arquivos locais ou URLs remotas
# True = usa arquivos locais, False = usa URLs (recomendado para Colab)
USAR_ARQUIVOS_LOCAIS = not IS_COLAB  # Automático: local se não for Colab

print("📚 DATASETS DISPONÍVEIS:")
print("="*60)
print(f"   📁 Fonte: {'Arquivos Locais' if USAR_ARQUIVOS_LOCAIS else 'URLs Remotas'}")
if USAR_ARQUIVOS_LOCAIS:
    print(f"   📂 Diretório: {BASE_PATH}")
print("="*60)
for ano, info in DATASETS_DISPONIVEIS.items():
    if USAR_ARQUIVOS_LOCAIS:
        existe = "✅" if os.path.exists(info['arquivo_local']) else "❌"
        print(f"   {existe} {ano}: {info['descricao']}")
    else:
        print(f"   📅 {ano}: {info['descricao']}")
print("="*60)

📚 DATASETS DISPONÍVEIS:
   📁 Fonte: Arquivos Locais
   📂 Diretório: c:\Users\Workstation\Desktop\Jupyter Notebook (.ipynb)\Data Storage (.csv)
   ✅ 2020: Queimadas 2020 - Ano crítico no Pantanal
   ✅ 2021: Queimadas 2021
   ✅ 2022: Queimadas 2022
   ✅ 2023: Queimadas 2023
   ✅ 2024: Queimadas 2024


### 2.2 Seleção do Modo de Processamento

**Opções disponíveis:**
- **INDIVIDUAL**: Processa apenas um ano selecionado
- **LOTE**: Processa múltiplos anos para comparação

In [4]:
# =============================================================================
# CONFIGURAÇÃO DO MODO DE PROCESSAMENTO
# =============================================================================
# Altere as variáveis abaixo para configurar o processamento

# MODO DE PROCESSAMENTO: 'INDIVIDUAL' ou 'LOTE'
MODO_PROCESSAMENTO = 'LOTE'  # Altere para 'INDIVIDUAL' se quiser processar apenas um ano

# ANOS PARA PROCESSAMENTO
# Para modo INDIVIDUAL: apenas o primeiro ano da lista será usado
# Para modo LOTE: todos os anos da lista serão processados
ANOS_SELECIONADOS = [2020, 2021, 2022, 2023, 2024]  # Modifique conforme necessário

# =============================================================================
# VALIDAÇÃO DA CONFIGURAÇÃO
# =============================================================================

if MODO_PROCESSAMENTO == 'INDIVIDUAL':
    ANOS_PARA_PROCESSAR = [ANOS_SELECIONADOS[0]]
    print(f"📊 MODO: INDIVIDUAL")
    print(f"   Ano selecionado: {ANOS_PARA_PROCESSAR[0]}")
elif MODO_PROCESSAMENTO == 'LOTE':
    ANOS_PARA_PROCESSAR = ANOS_SELECIONADOS
    print(f"📊 MODO: LOTE (Processamento em Lote)")
    print(f"   Anos selecionados: {ANOS_PARA_PROCESSAR}")
else:
    raise ValueError(f"Modo '{MODO_PROCESSAMENTO}' inválido. Use 'INDIVIDUAL' ou 'LOTE'")

# Validar se os anos existem
for ano in ANOS_PARA_PROCESSAR:
    if ano not in DATASETS_DISPONIVEIS:
        raise ValueError(f"Ano {ano} não disponível. Anos válidos: {list(DATASETS_DISPONIVEIS.keys())}")

print(f"\n✅ Configuração validada com sucesso!")
print(f"   Total de datasets a processar: {len(ANOS_PARA_PROCESSAR)}")

📊 MODO: LOTE (Processamento em Lote)
   Anos selecionados: [2020, 2021, 2022, 2023, 2024]

✅ Configuração validada com sucesso!
   Total de datasets a processar: 5


In [5]:
# =============================================================================
# FUNÇÃO DE CARREGAMENTO DE DADOS
# =============================================================================

def carregar_dataset(ano, verbose=True):
    """
    Carrega um dataset de queimadas para um ano específico.
    Suporta arquivos locais e URLs remotas.
    
    Args:
        ano: Ano do dataset (2020-2024)
        verbose: Se True, exibe mensagens de progresso
    
    Returns:
        DataFrame com os dados carregados e padronizados
    """
    if ano not in DATASETS_DISPONIVEIS:
        raise ValueError(f"Ano {ano} não disponível")
    
    info = DATASETS_DISPONIVEIS[ano]
    
    # Determinar fonte dos dados
    if USAR_ARQUIVOS_LOCAIS:
        fonte = info['arquivo_local']
        tipo_fonte = "local"
    else:
        fonte = info['url']
        tipo_fonte = "URL"
    
    if verbose:
        print(f"   📥 Carregando {ano} ({tipo_fonte})...", end=" ")
    
    # Tentar diferentes encodings
    encodings_to_try = ['utf-8', 'latin-1', 'iso-8859-1', 'cp1252']
    df = None
    
    for encoding in encodings_to_try:
        try:
            df = pd.read_csv(fonte, encoding=encoding)
            break
        except UnicodeDecodeError:
            continue
        except FileNotFoundError:
            raise FileNotFoundError(f"Arquivo não encontrado: {fonte}")
        except Exception as e:
            continue
    
    if df is None:
        raise ValueError(f"Não foi possível carregar o dataset de {ano}")
    
    # Padronizar nomes de colunas
    column_map = {
        "DataHora": "datahora",
        "Satelite": "satelite",
        "Pais": "pais",
        "Estado": "estado",
        "Municipio": "municipio",
        "Bioma": "bioma",
        "DiaSemChuva": "diasemchuva",
        "Precipitacao": "precipitacao",
        "RiscoFogo": "riscofogo",
        "FRP": "frp",
        "Latitude": "latitude",
        "Longitude": "longitude",
    }
    df = df.rename(columns={k: v for k, v in column_map.items() if k in df.columns})
    
    # Tratamento de valores especiais (-999 = dado ausente)
    if 'riscofogo' in df.columns:
        df['riscofogo'] = df['riscofogo'].replace(-999.0, np.nan)
        df['riscofogo'] = df['riscofogo'].replace(-999, np.nan)
    
    # Adicionar coluna de ano fonte
    df['ano_dataset'] = ano
    
    if verbose:
        print(f"✅ {len(df):,} registros")
    
    return df


def processar_features_temporais(df):
    """
    Processa e cria features temporais no DataFrame.
    """
    if 'datahora' in df.columns:
        df['datahora'] = pd.to_datetime(df['datahora'], errors='coerce')
        df['data'] = df['datahora'].dt.date
        df['hora'] = df['datahora'].dt.hour
        df['dia'] = df['datahora'].dt.day
        df['mes'] = df['datahora'].dt.month
        df['ano'] = df['datahora'].dt.year
        df['dia_semana'] = df['datahora'].dt.dayofweek
        df['nome_dia_semana'] = df['datahora'].dt.day_name()
        df['nome_mes'] = df['datahora'].dt.month_name()
        
        def get_season(month):
            if month in [12, 1, 2]:
                return 'Verão'
            elif month in [3, 4, 5]:
                return 'Outono'
            elif month in [6, 7, 8]:
                return 'Inverno'
            else:
                return 'Primavera'
        
        df['estacao'] = df['mes'].apply(get_season)
    
    return df

print("✅ Funções de carregamento definidas!")
print(f"   📁 Modo: {'Arquivos Locais' if USAR_ARQUIVOS_LOCAIS else 'URLs Remotas'}")

✅ Funções de carregamento definidas!
   📁 Modo: Arquivos Locais


In [6]:
# =============================================================================
# CARREGAMENTO DOS DADOS (Individual ou em Lote)
# =============================================================================

print(f"\n{'='*60}")
print(f"📥 CARREGANDO DATASETS - MODO: {MODO_PROCESSAMENTO}")
print(f"{'='*60}\n")

# Dicionário para armazenar datasets individuais
datasets_por_ano = {}

# Carregar cada ano selecionado
for ano in ANOS_PARA_PROCESSAR:
    try:
        df_ano = carregar_dataset(ano)
        df_ano = processar_features_temporais(df_ano)
        datasets_por_ano[ano] = df_ano
    except Exception as e:
        print(f"   ❌ Erro ao carregar {ano}: {str(e)}")

# Criar DataFrame combinado (para análises comparativas)
if len(datasets_por_ano) > 0:
    df_combinado = pd.concat(datasets_por_ano.values(), ignore_index=True)
    
    # Para compatibilidade com código existente, criar df e df_original
    if MODO_PROCESSAMENTO == 'INDIVIDUAL':
        df_original = datasets_por_ano[ANOS_PARA_PROCESSAR[0]].copy()
        df = df_original.copy()
    else:
        df_original = df_combinado.copy()
        df = df_combinado.copy()
    
    print(f"\n{'='*60}")
    print(f"✅ RESUMO DO CARREGAMENTO")
    print(f"{'='*60}")
    print(f"   📊 Anos carregados: {list(datasets_por_ano.keys())}")
    print(f"   📈 Total de registros: {len(df_combinado):,}")
    print(f"   💾 Memória total: {df_combinado.memory_usage(deep=True).sum() / 1024**2:.2f} MB")
    
    # Resumo por ano
    print(f"\n   📅 Registros por ano:")
    for ano, df_ano in datasets_por_ano.items():
        print(f"      {ano}: {len(df_ano):,} focos")
else:
    raise ValueError("Nenhum dataset foi carregado com sucesso!")


📥 CARREGANDO DATASETS - MODO: LOTE

   📥 Carregando 2020 (local)... ✅ 234,345 registros
   📥 Carregando 2021 (local)... ✅ 191,190 registros
   📥 Carregando 2022 (local)... ✅ 38,840 registros
   📥 Carregando 2023 (local)... ✅ 142,381 registros
   📥 Carregando 2024 (local)... ✅ 313,571 registros

✅ RESUMO DO CARREGAMENTO
   📊 Anos carregados: [2020, 2021, 2022, 2023, 2024]
   📈 Total de registros: 920,327
   💾 Memória total: 524.54 MB

   📅 Registros por ano:
      2020: 234,345 focos
      2021: 191,190 focos
      2022: 38,840 focos
      2023: 142,381 focos
      2024: 313,571 focos


In [7]:
# Visualizar primeiras linhas do dataset combinado/selecionado
print("\n🔍 Primeiras 5 linhas do dataset:")
display(df.head())

print(f"\n📋 Colunas disponíveis: {list(df.columns)}")


🔍 Primeiras 5 linhas do dataset:


datahora   satelite    pais              estado municipio  \
0 2020-01-01 14:00:00  TERRA_M-T  Brasil  MATO GROSSO DO SUL   CORUMBÁ   
1 2020-01-01 14:00:00  TERRA_M-T  Brasil  MATO GROSSO DO SUL   CORUMBÁ   
2 2020-01-01 14:00:00  TERRA_M-T  Brasil  MATO GROSSO DO SUL   CORUMBÁ   
3 2020-01-01 14:00:00  TERRA_M-T  Brasil  MATO GROSSO DO SUL   CORUMBÁ   
4 2020-01-01 14:00:00  TERRA_M-T  Brasil  MATO GROSSO DO SUL   CORUMBÁ   

      bioma  diasemchuva  precipitacao  riscofogo   frp  latitude  longitude  \
0  Pantanal            0           0.1        0.3  28.1   -19.700    -57.252   
1  Pantanal            0           0.1        0.3  10.8   -19.709    -57.254   
2  Pantanal            0           0.1        0.3  14.7   -19.701    -57.243   
3  Pantanal            0           0.1        0.3   9.1   -19.710    -57.244   
4  Pantanal            1           0.2        0.3  34.7   -19.684    -57.230   

   ano_dataset        data  hora  dia  mes   ano  dia_semana nome_dia_semana  \
0         2020  2020-01-01    14    1    1  2020           2       Wednesday   
1         2020  2020-01-01    14    1    1  2020           2       Wednesday   
2         2020  2020-01-01    14    1    1  2020           2       Wednesday   
3         2020  2020-01-01    14    1    1  2020           2       Wednesday   
4         2020  2020-01-01    14    1    1  2020           2       Wednesday   

  nome_mes estacao  
0  January   Verão  
1  January   Verão  
2  January   Verão  
3  January   Verão  
4  January   Verão


📋 Colunas disponíveis: ['datahora', 'satelite', 'pais', 'estado', 'municipio', 'bioma', 'diasemchuva', 'precipitacao', 'riscofogo', 'frp', 'latitude', 'longitude', 'ano_dataset', 'data', 'hora', 'dia', 'mes', 'ano', 'dia_semana', 'nome_dia_semana', 'nome_mes', 'estacao']


In [8]:
# Informações sobre tipos de dados
print("\n📋 Informações sobre o dataset:")
df.info()


📋 Informações sobre o dataset:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 920327 entries, 0 to 920326
Data columns (total 22 columns):
 #   Column           Non-Null Count   Dtype         
---  ------           --------------   -----         
 0   datahora         920327 non-null  datetime64[ns]
 1   satelite         920327 non-null  object        
 2   pais             920327 non-null  object        
 3   estado           920327 non-null  object        
 4   municipio        920327 non-null  object        
 5   bioma            920327 non-null  object        
 6   diasemchuva      920327 non-null  int64         
 7   precipitacao     920327 non-null  float64       
 8   riscofogo        894495 non-null  float64       
 9   frp              667057 non-null  float64       
 10  latitude         920327 non-null  float64       
 11  longitude        920327 non-null  float64       
 12  ano_dataset      920327 non-null  int64         
 13  data             920327 non-null  object  

In [9]:
# Estatísticas descritivas
print("\n📊 Estatísticas Descritivas:")
display(df.describe())


📊 Estatísticas Descritivas:


datahora    diasemchuva   precipitacao  \
count                         920327  920327.000000  920327.000000   
mean   2022-10-05 03:22:35.055399680      17.178211       0.738433   
min              2020-01-01 14:00:00    -999.000000       0.000000   
25%              2020-11-25 18:12:00       4.000000       0.000000   
50%              2022-11-30 11:57:03       9.000000       0.000000   
75%              2024-06-20 17:17:00      22.000000       0.000000   
max              2024-12-31 18:19:00     140.000000      97.400000   
std                              NaN      29.696643       3.668633   

           riscofogo            frp       latitude      longitude  \
count  894495.000000  667057.000000  920327.000000  920327.000000   
mean        0.740889      49.732585     -19.166993     -57.021218   
min         0.000000      -0.700000     -22.136400     -58.166901   
25%         0.570000       5.700000     -19.806060     -57.522839   
50%         0.900000      17.200000     -19.170000     -57.260040   
75%         1.000000      68.800000     -18.365520     -56.520000   
max         1.000000    5339.400000     -17.169100     -54.922810   
std         0.320978      95.818800       1.024747       0.666422   

         ano_dataset           hora            dia            mes  \
count  920327.000000  920327.000000  920327.000000  920327.000000   
mean     2022.119135      12.530799      15.562108       8.200064   
min      2020.000000       0.000000       1.000000       1.000000   
25%      2020.000000       5.000000       8.000000       7.000000   
50%      2022.000000      16.000000      15.000000       9.000000   
75%      2024.000000      17.000000      23.000000      10.000000   
max      2024.000000      23.000000      31.000000      12.000000   
std         1.652167       7.080034       8.862659       2.449327   

                 ano     dia_semana  
count  920327.000000  920327.000000  
mean     2022.119135       2.996043  
min      2020.000000       0.000000  
25%      2020.000000       1.000000  
50%      2022.000000       3.000000  
75%      2024.000000       5.000000  
max      2024.000000       6.000000  
std         1.652167       1.984474

In [10]:
# Verificação de valores ausentes
print("\n🔍 Análise de Valores Ausentes:")
missing_data = pd.DataFrame({
    'Coluna': df.columns,
    'Valores_Ausentes': df.isnull().sum(),
    'Percentual': (df.isnull().sum() / len(df)) * 100
})
missing_data = missing_data[missing_data['Valores_Ausentes'] > 0].sort_values('Valores_Ausentes', ascending=False)

if len(missing_data) > 0:
    display(missing_data)
else:
    print("✅ Nenhum valor ausente detectado!")


🔍 Análise de Valores Ausentes:


Coluna  Valores_Ausentes  Percentual
frp              frp            253270   27.519566
riscofogo  riscofogo             25832    2.806828

## 3️⃣ Análise Comparativa Multi-Ano

### 3.1 Comparação de Focos por Ano

In [11]:
# =============================================================================
# COMPARAÇÃO ENTRE ANOS (apenas no modo LOTE)
# =============================================================================

if MODO_PROCESSAMENTO == 'LOTE' and len(datasets_por_ano) > 1:
    print("📊 ANÁLISE COMPARATIVA ENTRE ANOS")
    print("="*60)
    
    # Criar DataFrame resumo por ano
    resumo_anos = []
    for ano, df_ano in datasets_por_ano.items():
        resumo = {
            'Ano': ano,
            'Total_Focos': len(df_ano),
            'FRP_Medio': df_ano['frp'].mean() if 'frp' in df_ano.columns else np.nan,
            'FRP_Maximo': df_ano['frp'].max() if 'frp' in df_ano.columns else np.nan,
            'Estados_Afetados': df_ano['estado'].nunique() if 'estado' in df_ano.columns else np.nan,
            'Municipios_Afetados': df_ano['municipio'].nunique() if 'municipio' in df_ano.columns else np.nan
        }
        resumo_anos.append(resumo)
    
    df_resumo_anos = pd.DataFrame(resumo_anos)
    display(df_resumo_anos)
    
    # Gráfico de barras - Total de focos por ano
    fig = px.bar(
        df_resumo_anos,
        x='Ano',
        y='Total_Focos',
        title='🔥 Total de Focos de Queimadas por Ano',
        labels={'Ano': 'Ano', 'Total_Focos': 'Número de Focos'},
        color='Total_Focos',
        color_continuous_scale='Reds',
        text='Total_Focos'
    )
    fig.update_traces(texttemplate='%{text:,.0f}', textposition='outside')
    fig.update_layout(height=500)
    fig.show()
    
    # Calcular variação percentual ano a ano
    print("\n📈 Variação Ano a Ano:")
    df_resumo_anos_sorted = df_resumo_anos.sort_values('Ano')
    for i in range(1, len(df_resumo_anos_sorted)):
        ano_atual = df_resumo_anos_sorted.iloc[i]['Ano']
        ano_anterior = df_resumo_anos_sorted.iloc[i-1]['Ano']
        focos_atual = df_resumo_anos_sorted.iloc[i]['Total_Focos']
        focos_anterior = df_resumo_anos_sorted.iloc[i-1]['Total_Focos']
        variacao = ((focos_atual - focos_anterior) / focos_anterior) * 100
        emoji = "📈" if variacao > 0 else "📉"
        print(f"   {emoji} {ano_anterior} → {ano_atual}: {variacao:+.1f}%")

else:
    print("ℹ️ Comparação entre anos disponível apenas no modo LOTE com múltiplos anos")

📊 ANÁLISE COMPARATIVA ENTRE ANOS


Ano  Total_Focos  FRP_Medio  FRP_Maximo  Estados_Afetados  \
0  2020       234345  24.425586      3161.6                 1   
1  2021       191190  29.303959      4814.4                 1   
2  2022        38840  38.858257      1609.5                 1   
3  2023       142381  85.360436      4022.3                 1   
4  2024       313571  50.007853      5339.4                 1   

   Municipios_Afetados  
0                   10  
1                    9  
2                   10  
3                    9  
4                   11


📈 Variação Ano a Ano:
   📉 2020.0 → 2021.0: -18.4%
   📉 2021.0 → 2022.0: -79.7%
   📈 2022.0 → 2023.0: +266.6%
   📈 2023.0 → 2024.0: +120.2%


### 3.2 Comparação Mensal entre Anos

In [12]:
# =============================================================================
# COMPARAÇÃO MENSAL ENTRE ANOS
# =============================================================================

if MODO_PROCESSAMENTO == 'LOTE' and len(datasets_por_ano) > 1:
    # Criar análise mensal para cada ano
    dados_mensais = []
    for ano, df_ano in datasets_por_ano.items():
        if 'mes' in df_ano.columns:
            focos_mes = df_ano.groupby('mes').size().reset_index(name='total_focos')
            focos_mes['ano'] = ano
            dados_mensais.append(focos_mes)
    
    if dados_mensais:
        df_mensal = pd.concat(dados_mensais, ignore_index=True)
        
        # Gráfico de linhas comparativo
        fig = px.line(
            df_mensal,
            x='mes',
            y='total_focos',
            color='ano',
            title='📊 Comparação de Focos por Mês entre Anos',
            labels={'mes': 'Mês', 'total_focos': 'Número de Focos', 'ano': 'Ano'},
            markers=True
        )
        fig.update_layout(
            xaxis=dict(tickmode='linear', dtick=1),
            height=500,
            legend_title_text='Ano'
        )
        fig.show()
        
        # Heatmap de focos por mês e ano
        pivot_mensal = df_mensal.pivot(index='ano', columns='mes', values='total_focos')
        
        fig2 = px.imshow(
            pivot_mensal,
            title='🗓️ Heatmap: Focos por Mês e Ano',
            labels=dict(x="Mês", y="Ano", color="Focos"),
            color_continuous_scale='YlOrRd',
            aspect='auto'
        )
        fig2.update_layout(height=400)
        fig2.show()
        
        # Identificar mês crítico por ano
        print("\n🔥 Mês com mais focos por ano:")
        for ano in sorted(datasets_por_ano.keys()):
            df_ano_mes = df_mensal[df_mensal['ano'] == ano]
            if len(df_ano_mes) > 0:
                mes_pico = df_ano_mes.loc[df_ano_mes['total_focos'].idxmax()]
                print(f"   {ano}: Mês {int(mes_pico['mes'])} ({mes_pico['total_focos']:,} focos)")

else:
    # Análise mensal para modo individual
    if 'mes' in df.columns:
        focos_por_mes = df.groupby('mes').size().reset_index(name='total_focos')
        ano_atual = ANOS_PARA_PROCESSAR[0] if MODO_PROCESSAMENTO == 'INDIVIDUAL' else 'Todos'
        
        fig = px.bar(
            focos_por_mes,
            x='mes',
            y='total_focos',
            title=f'📊 Distribuição de Focos de Queimadas por Mês ({ano_atual})',
            labels={'mes': 'Mês', 'total_focos': 'Número de Focos'},
            color='total_focos',
            color_continuous_scale='Reds'
        )
        fig.update_layout(xaxis=dict(tickmode='linear', dtick=1), height=500)
        fig.show()
        
        mes_pico = focos_por_mes.loc[focos_por_mes['total_focos'].idxmax()]
        print(f"\n🔥 Mês com maior número de focos: {int(mes_pico['mes'])} ({mes_pico['total_focos']:,} focos)")


🔥 Mês com mais focos por ano:
   2020: Mês 9 (58,932 focos)
   2021: Mês 9 (77,774 focos)
   2022: Mês 5 (9,551 focos)
   2023: Mês 11 (83,888 focos)
   2024: Mês 8 (105,332 focos)


### 3.3 Série Temporal Comparativa

In [13]:
# =============================================================================
# SÉRIE TEMPORAL DIÁRIA
# =============================================================================

if 'data' in df.columns:
    focos_diarios = df.groupby(['data', 'ano_dataset']).size().reset_index(name='total_focos')
    focos_diarios['data'] = pd.to_datetime(focos_diarios['data'])
    
    if MODO_PROCESSAMENTO == 'LOTE' and len(datasets_por_ano) > 1:
        # Gráfico com múltiplas linhas por ano
        fig = px.line(
            focos_diarios,
            x='data',
            y='total_focos',
            color='ano_dataset',
            title='📈 Série Temporal de Focos de Queimadas - Comparativo',
            labels={'data': 'Data', 'total_focos': 'Número de Focos', 'ano_dataset': 'Ano'},
        )
    else:
        # Gráfico simples
        fig = px.line(
            focos_diarios,
            x='data',
            y='total_focos',
            title=f'📈 Série Temporal de Focos de Queimadas',
            labels={'data': 'Data', 'total_focos': 'Número de Focos'},
        )
        fig.update_traces(line_color='#ff4444', line_width=2)
    
    fig.update_layout(height=500)
    fig.show()
    
    print(f"\n📊 Estatísticas da Série Temporal:")
    print(f"   Média diária: {focos_diarios['total_focos'].mean():.1f} focos")
    print(f"   Mediana: {focos_diarios['total_focos'].median():.1f} focos")
    print(f"   Desvio padrão: {focos_diarios['total_focos'].std():.1f} focos")
    print(f"   Máximo: {focos_diarios['total_focos'].max():,} focos")


📊 Estatísticas da Série Temporal:
   Média diária: 551.4 focos
   Mediana: 87.0 focos
   Desvio padrão: 1339.0 focos
   Máximo: 14,930 focos


## 4️⃣ Análise Espacial

### 4.1 Análise por Estado

In [14]:
# Análise por estado
if 'estado' in df.columns:
    if MODO_PROCESSAMENTO == 'LOTE' and len(datasets_por_ano) > 1:
        # Comparação de estados por ano
        focos_estado_ano = df.groupby(['estado', 'ano_dataset']).size().reset_index(name='total_focos')
        top_estados = df['estado'].value_counts().head(10).index.tolist()
        focos_estado_ano_top = focos_estado_ano[focos_estado_ano['estado'].isin(top_estados)]
        
        fig = px.bar(
            focos_estado_ano_top,
            x='estado',
            y='total_focos',
            color='ano_dataset',
            title='🗺️ Top 10 Estados - Comparativo por Ano',
            labels={'estado': 'Estado', 'total_focos': 'Número de Focos', 'ano_dataset': 'Ano'},
            barmode='group'
        )
        fig.update_layout(height=500, xaxis_tickangle=-45)
        fig.show()
    else:
        focos_por_estado = df['estado'].value_counts().reset_index()
        focos_por_estado.columns = ['estado', 'total_focos']
        
        fig = px.bar(
            focos_por_estado.head(10),
            x='estado',
            y='total_focos',
            title='🗺️ Top 10 Estados com Maior Número de Focos',
            labels={'estado': 'Estado', 'total_focos': 'Número de Focos'},
            color='total_focos',
            color_continuous_scale='OrRd'
        )
        fig.update_layout(height=500)
        fig.show()
    
    print(f"\n🔥 Estados mais afetados (total):")
    focos_por_estado = df['estado'].value_counts().head(5)
    for idx, (estado, count) in enumerate(focos_por_estado.items()):
        print(f"   {idx+1}. {estado}: {count:,} focos")


🔥 Estados mais afetados (total):
   1. MATO GROSSO DO SUL: 920,327 focos


### 4.2 Análise por Município

In [15]:
# Análise por município
if 'municipio' in df.columns:
    focos_por_municipio = df['municipio'].value_counts().reset_index()
    focos_por_municipio.columns = ['municipio', 'total_focos']
    
    fig = px.bar(
        focos_por_municipio.head(15),
        x='municipio',
        y='total_focos',
        title='🏙️ Top 15 Municípios com Maior Número de Focos',
        labels={'municipio': 'Município', 'total_focos': 'Número de Focos'},
        color='total_focos',
        color_continuous_scale='YlOrRd'
    )
    
    fig.update_layout(height=500, xaxis_tickangle=-45)
    fig.show()

### 4.3 Análise de Intensidade (FRP - Fire Radiative Power)

In [16]:
# Análise do FRP (Fire Radiative Power)
if 'frp' in df.columns:
    frp_clean = df['frp'].dropna()
    frp_clean = frp_clean[frp_clean > 0]
    
    if MODO_PROCESSAMENTO == 'LOTE' and len(datasets_por_ano) > 1:
        # Box plot comparativo por ano
        df_frp = df[df['frp'] > 0][['frp', 'ano_dataset']].dropna()
        
        fig = px.box(
            df_frp,
            x='ano_dataset',
            y='frp',
            title='🔥 Distribuição do FRP por Ano',
            labels={'ano_dataset': 'Ano', 'frp': 'FRP (MW)'},
            color='ano_dataset'
        )
        fig.update_layout(height=500)
        fig.show()
        
        # Estatísticas por ano
        print("\n📊 Estatísticas do FRP por Ano:")
        for ano in sorted(datasets_por_ano.keys()):
            df_ano_frp = datasets_por_ano[ano]['frp'].dropna()
            df_ano_frp = df_ano_frp[df_ano_frp > 0]
            print(f"   {ano}: Média={df_ano_frp.mean():.2f} MW, Máx={df_ano_frp.max():.2f} MW")
    else:
        # Análise simples
        fig = make_subplots(
            rows=1, cols=2,
            subplot_titles=('Distribuição do FRP', 'Boxplot do FRP')
        )
        
        fig.add_trace(
            go.Histogram(x=frp_clean, nbinsx=50, name='FRP', marker_color='orangered'),
            row=1, col=1
        )
        
        fig.add_trace(
            go.Box(y=frp_clean, name='FRP', marker_color='coral'),
            row=1, col=2
        )
        
        fig.update_layout(
            title_text='🔥 Análise de Intensidade dos Focos (FRP)',
            height=400,
            showlegend=False
        )
        fig.show()
    
    print(f"\n📊 Estatísticas Gerais do FRP:")
    print(f"   Média: {frp_clean.mean():.2f} MW")
    print(f"   Mediana: {frp_clean.median():.2f} MW")
    print(f"   Máximo: {frp_clean.max():.2f} MW")


📊 Estatísticas do FRP por Ano:
   2020: Média=24.43 MW, Máx=3161.60 MW
   2021: Média=29.31 MW, Máx=4814.40 MW
   2022: Média=38.86 MW, Máx=1609.50 MW
   2023: Média=85.39 MW, Máx=4022.30 MW
   2024: Média=50.05 MW, Máx=5339.40 MW

📊 Estatísticas Gerais do FRP:
   Média: 49.76 MW
   Mediana: 17.20 MW
   Máximo: 5339.40 MW


### 4.4 Mapa de Calor Geoespacial

In [17]:
# Criar mapa interativo com Folium
if 'latitude' in df.columns and 'longitude' in df.columns:
    df_map = df[['latitude', 'longitude']].dropna()
    
    # Amostrar dados se muito grande
    if len(df_map) > 10000:
        df_map = df_map.sample(n=10000, random_state=42)
    
    center_lat = df_map['latitude'].mean()
    center_lon = df_map['longitude'].mean()
    
    m = folium.Map(
        location=[center_lat, center_lon],
        zoom_start=5,
        tiles='OpenStreetMap'
    )
    
    heat_data = [[row['latitude'], row['longitude']] for idx, row in df_map.iterrows()]
    HeatMap(heat_data, radius=10, blur=15, max_zoom=13).add_to(m)
    
    periodo = f"{min(ANOS_PARA_PROCESSAR)}-{max(ANOS_PARA_PROCESSAR)}" if len(ANOS_PARA_PROCESSAR) > 1 else str(ANOS_PARA_PROCESSAR[0])
    print(f"\n🗺️ Mapa de calor criado - Período: {periodo}")
    print(f"   📍 Centro: ({center_lat:.4f}, {center_lon:.4f})")
    print(f"   📊 Pontos plotados: {len(df_map):,}")
    
    display(m)


🗺️ Mapa de calor criado - Período: 2020-2024
   📍 Centro: (-19.1565, -57.0196)
   📊 Pontos plotados: 10,000


### 4.5 Análise de Correlação

In [18]:
# Selecionar apenas colunas numéricas para correlação
numeric_cols = df.select_dtypes(include=[np.number]).columns.tolist()

# Remover colunas de ID ou irrelevantes
cols_to_exclude = ['ano', 'id', 'ano_dataset']
numeric_cols = [col for col in numeric_cols if col not in cols_to_exclude]

if len(numeric_cols) > 1:
    correlation_matrix = df[numeric_cols].corr()
    
    fig = px.imshow(
        correlation_matrix,
        title='🔥 Matriz de Correlação entre Variáveis Numéricas',
        color_continuous_scale='RdBu_r',
        aspect='auto',
        labels=dict(color="Correlação")
    )
    
    fig.update_layout(height=600, width=800)
    fig.show()
    
    print("\n📊 Principais correlações identificadas:")
    corr_pairs = []
    for i in range(len(correlation_matrix.columns)):
        for j in range(i+1, len(correlation_matrix.columns)):
            corr_pairs.append((
                correlation_matrix.columns[i],
                correlation_matrix.columns[j],
                correlation_matrix.iloc[i, j]
            ))
    
    corr_pairs_sorted = sorted(corr_pairs, key=lambda x: abs(x[2]), reverse=True)
    for var1, var2, corr in corr_pairs_sorted[:5]:
        print(f"   {var1} ↔ {var2}: {corr:.3f}")


📊 Principais correlações identificadas:
   precipitacao ↔ riscofogo: -0.366
   latitude ↔ longitude: 0.353
   diasemchuva ↔ riscofogo: 0.273
   diasemchuva ↔ mes: -0.161
   longitude ↔ mes: 0.139


## 5️⃣ Pré-processamento e Feature Engineering

### 5.1 Tratamento de Valores Ausentes

### 4.3 Codificação de Variáveis Categóricas

### 5.2 Feature Engineering Avançado

## 5️⃣ Análise de Clusterização (Aprendizado Não Supervisionado)

### 5.1 Preparação dos Dados para Clustering

### 5.3 Codificação de Variáveis Categóricas

### 5.2 Método do Cotovelo (Elbow Method)

## 6️⃣ Análise de Clusterização (Aprendizado Não Supervisionado)

### 6.1 Preparação dos Dados para Clustering

### 5.3 Aplicação do K-Means

### 6.2 Método do Cotovelo (Elbow Method)

### 5.4 Visualização dos Clusters

### 6.3 Aplicação do K-Means

In [19]:
# Visualização espacial dos clusters
if 'latitude' in df_clustering.columns and 'longitude' in df_clustering.columns:
    sample_size = min(10000, len(df_clustering))
    df_sample = df_clustering.sample(n=sample_size, random_state=42)
    
    fig = px.scatter_mapbox(
        df_sample,
        lat='latitude',
        lon='longitude',
        color='cluster',
        title=f'🗺️ Distribuição Espacial dos Clusters (K={optimal_k})',
        mapbox_style='open-street-map',
        zoom=5,
        height=600,
        color_continuous_scale='Viridis'
    )
    
    fig.show()

NameError: name 'df_clustering' is not defined

### 6.4 Visualização dos Clusters

In [ ]:
# Criar variável target baseada em FRP
print("\n🎯 Preparando dados para modelagem supervisionada...")

df_supervised = df_ml.copy()

# Criar target: classificar focos por intensidade
if 'frp' in df_supervised.columns:
    # Definir limiares
    q25 = df_supervised['frp'].quantile(0.25)
    q75 = df_supervised['frp'].quantile(0.75)
    
    # Criar classes: 0=Baixa, 1=Média, 2=Alta
    df_supervised['intensidade_classe'] = pd.cut(
        df_supervised['frp'],
        bins=[-np.inf, q25, q75, np.inf],
        labels=[0, 1, 2]
    )
    
    target_col = 'intensidade_classe'
    print(f"   ✅ Variável target criada: {target_col}")
    print(f"\n   Distribuição das classes:")
    print(df_supervised[target_col].value_counts().sort_index())
    
    # Selecionar features
    exclude_cols = ['datahora', 'data', 'nome_dia_semana', 'nome_mes', target_col, 
                   'cluster', 'frp_categoria', 'intensidade_classe']
    
    feature_cols = [col for col in df_supervised.select_dtypes(include=[np.number]).columns 
                   if col not in exclude_cols]
    
    # Remover linhas com valores ausentes
    df_model = df_supervised[[target_col] + feature_cols].dropna()
    
    print(f"\n   📊 Dataset para modelagem:")
    print(f"      Amostras: {len(df_model):,}")
    print(f"      Features: {len(feature_cols)}")
else:
    print("   ⚠️ FRP não disponível")
    target_col = None

### 6.2 Divisão Treino/Teste

## 7️⃣ Modelagem Preditiva (Aprendizado Supervisionado)

### 7.1 Preparação dos Dados

### 6.3 Random Forest

### 7.2 Divisão Treino/Teste

### 6.4 Importância das Features

### 7.3 Random Forest

### 6.5 XGBoost

### 7.4 Importância das Features

## 7️⃣ Síntese de Insights e Recomendações

### 7.1 Principais Insights

### 7.5 XGBoost

## 8️⃣ Conclusões e Trabalhos Futuros

## 8️⃣ Síntese de Insights e Recomendações

### 8.1 Principais Insights